In [3]:
import netflow
import socket
sock = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)
sock.bind(("0.0.0.0", 2055))
payload, client = sock.recvfrom(4096)  # experimental, tested with 1464 bytes
p = netflow.parse_packet(payload)  # Test result: <ExportPacket v5 with 30 records>
print(p.header.version)  # Test result: 5

OSError: [Errno 98] Address already in use

In [2]:
!pip install netflow

In [1]:
#!/usr/bin/env python3

"""
Reference collector script for NetFlow v1, v5, and v9 Python package.
This file belongs to https://github.com/bitkeks/python-netflow-v9-softflowd.
Copyright 2016-2020 Dominik Pataky <software+pynetflow@dpataky.eu>
Licensed under MIT License. See LICENSE.
"""
import argparse
import gzip
import json
import logging
import queue
import socket
import socketserver
import threading
import time
from collections import namedtuple

import sys

sys.path.append('/home/yuhao/Study/master thesis/netflow-generator')

from package.ipfix import IPFIXTemplateNotRecognized
from package.utils import UnknownExportVersion, parse_packet
from package.v9 import V9TemplateNotRecognized

RawPacket = namedtuple('RawPacket', ['ts', 'client', 'data'])
ParsedPacket = namedtuple('ParsedPacket', ['ts', 'client', 'export'])

# Amount of time to wait before dropping an undecodable ExportPacket
PACKET_TIMEOUT = 60 * 60

logger = logging.getLogger("netflow-collector")
ch = logging.StreamHandler()
formatter = logging.Formatter('%(asctime)s - %(levelname)s - %(message)s')
ch.setFormatter(formatter)
logger.addHandler(ch)


class QueuingRequestHandler(socketserver.BaseRequestHandler):
    def handle(self):
        data = self.request[0]  # get content, [1] would be the socket
        self.server.queue.put(RawPacket(time.time(), self.client_address, data))
        logger.debug(
            "Received %d bytes of data from %s", len(data), self.client_address
        )


class QueuingUDPListener(socketserver.ThreadingUDPServer):
    """A threaded UDP server that adds a (time, data) tuple to a queue for
    every request it sees
    """

    def __init__(self, interface, queue):
        self.queue = queue

        # If IPv6 interface addresses are used, override the default AF_INET family
        if ":" in interface[0]:
            self.address_family = socket.AF_INET6

        super().__init__(interface, QueuingRequestHandler)


class ThreadedNetFlowListener(threading.Thread):
    """A thread that listens for incoming NetFlow packets, processes them, and
    makes them available to consumers.
    - When initialized, will start listening for NetFlow packets on the provided
      host and port and queuing them for processing.
    - When started, will start processing and parsing queued packets.
    - When stopped, will shut down the listener and stop processing.
    - When joined, will wait for the listener to exit
    For example, a simple script that outputs data until killed with CTRL+C:
    >>> listener = ThreadedNetFlowListener('0.0.0.0', 2055)
    >>> print("Listening for NetFlow packets")
    >>> listener.start() # start processing packets
    >>> try:
    ...     while True:
    ...         ts, export = listener.get()
    ...         print("Time: {}".format(ts))
    ...         for f in export.flows:
    ...             print(" - {IPV4_SRC_ADDR} sent data to {IPV4_DST_ADDR}"
    ...                   "".format(**f))
    ... finally:
    ...     print("Stopping...")
    ...     listener.stop()
    ...     listener.join()
    ...     print("Stopped!")
    """

    def __init__(self, host: str, port: int):
        logger.info("Starting the NetFlow listener on {}:{}".format(host, port))
        self.output = queue.Queue()
        self.input = queue.Queue()
        self.server = QueuingUDPListener((host, port), self.input)
        self.thread = threading.Thread(target=self.server.serve_forever)
        self.thread.start()
        self._shutdown = threading.Event()
        super().__init__()

    def get(self, block=True, timeout=None) -> ParsedPacket:
        """Get a processed flow.
        If optional args 'block' is true and 'timeout' is None (the default),
        block if necessary until a flow is available. If 'timeout' is
        a non-negative number, it blocks at most 'timeout' seconds and raises
        the queue.Empty exception if no flow was available within that time.
        Otherwise ('block' is false), return a flow if one is immediately
        available, else raise the queue.Empty exception ('timeout' is ignored
        in that case).
        """
        return self.output.get(block, timeout)

    def run(self):
        # Process packets from the queue
        try:
            templates = {"netflow": {}, "ipfix": {}}
            to_retry = []
            while not self._shutdown.is_set():
                try:
                    # 0.5s delay to limit CPU usage while waiting for new packets
                    pkt = self.input.get(block=True, timeout=0.5)  # type: RawPacket
                except queue.Empty:
                    continue

                try:
                    # templates is passed as reference, updated in V9ExportPacket
                    export = parse_packet(pkt.data, templates)
                except UnknownExportVersion as e:
                    logger.error("%s, ignoring the packet", e)
                    continue
                except (V9TemplateNotRecognized, IPFIXTemplateNotRecognized):
                    # TODO: differentiate between v9 and IPFIX, use separate to_retry lists
                    if time.time() - pkt.ts > PACKET_TIMEOUT:
                        logger.warning("Dropping an old and undecodable v9/IPFIX ExportPacket")
                    else:
                        to_retry.append(pkt)
                        logger.debug("Failed to decode a v9/IPFIX ExportPacket - will "
                                     "re-attempt when a new template is discovered")
                    continue

                if export.header.version == 10:
                    logger.debug("Processed an IPFIX ExportPacket with length %d.", export.header.length)
                else:
                    logger.debug("Processed a v%d ExportPacket with %d flows.",
                                 export.header.version, export.header.count)

                # If any new templates were discovered, dump the unprocessable
                # data back into the queue and try to decode them again
                if export.header.version in [9, 10] and export.contains_new_templates and to_retry:
                    logger.debug("Received new template(s)")
                    logger.debug("Will re-attempt to decode %d old v9/IPFIX ExportPackets", len(to_retry))
                    for p in to_retry:
                        self.input.put(p)
                    to_retry.clear()

                self.output.put(ParsedPacket(pkt.ts, pkt.client, export))
        finally:
            # Only reached when while loop ends
            self.server.shutdown()
            self.server.server_close()

    def stop(self):
        logger.info("Shutting down the NetFlow listener")
        self._shutdown.set()

    def join(self, timeout=None):
        self.thread.join(timeout=timeout)
        super().join(timeout=timeout)


def get_export_packets(host: str, port: int) -> ParsedPacket:
    """A threaded generator that will yield ExportPacket objects until it is killed
    """
    listener = ThreadedNetFlowListener(host, port)
    listener.start()
    try:
        while True:
            yield listener.get()
    finally:
        listener.stop()
        listener.join()


if __name__ == "netflow.collector":
    logger.error("The collector is currently meant to be used as a CLI tool only.")
    logger.error("Use 'python3 -m netflow.collector -h' in your console for additional help.")



try:
        # With every parsed flow a new line is appended to the output file. In previous versions, this was implemented
        # by storing the whole data dict in memory and dumping it regularly onto disk. This was extremely fragile, as
        # it a) consumed a lot of memory and CPU (dropping packets since storing one flow took longer than the arrival
        # of the next flow) and b) broke the exported JSON file, if the collector crashed during the write process,
        # rendering all collected flows during the runtime of the collector useless (the file contained one large JSON
        # dict which represented the 'data' dict).

        # In this new approach, each received flow is parsed as usual, but it gets appended to a gzipped file each time.
        # All in all, this improves in three aspects:
        # 1. collected flow data is not stored in memory any more
        # 2. received and parsed flows are persisted reliably
        # 3. the disk usage of files with JSON and its full strings as keys is reduced by using gzipped files
        # This also means that the files have to be handled differently, because they are gzipped and not formatted as
        # one single big JSON dump, but rather many little JSON dumps, separated by line breaks.
        for ts, client, export in get_export_packets("0.0.0.0", 3000):
            entry = {ts: {
                "client": client,
                "header": export.header.to_dict(),
                "flows": [flow.data for flow in export.flows]}
            }
            line = json.dumps(entry).encode() + b"\n"  # byte encoded line
            with gzip.open("{}.gz".format(int(time.time())), "ab") as fh:  # open as append, not reading the whole file
                fh.write(line)
except KeyboardInterrupt:
        logger.info("Received KeyboardInterrupt, passing through")
        pass

In [3]:

#endcoding=utf-8
from socket import *
 
udpSocket=socket(AF_INET,SOCK_DGRAM)
 
udpSocket.bind(("",7788))  #参数是元组的形式
#使用udp发送的数据，在每一次的时候都需要写上接收方的IP和port
udpSocket.sendto("0009000a000000035c9f55980000000100000000000000400400000e00080004000c000400150004001600040001000400020004000a0004000e000400070002000b00020004000100060001003c000100050001000000400800000e001b0010001c001000150004001600040001000400020004000a0004000e000400070002000b00020004000100060001003c000100050001040001447f0000017f000001fb3c1aaafb3c18fd000190100000004b00000000000000000050942c061b04007f0000017f000001fb3c1aaafb3c18fd00000f94000000360000000000000000942c0050061f04007f0000017f000001fb3c1cfcfb3c1a9b0000d3fc0000002a000000000000000000509434061b04007f0000017f000001fb3c1cfcfb3c1a9b00000a490000001e000000000000000094340050061f04007f0000017f000001fb3bb82cfb3ba48b000002960000000300000000000000000050942a061904007f0000017f000001fb3bb82cfb3ba48b00000068000000020000000000000000942a0050061104007f0000017f000001fb3c1900fb3c18fe0000004c0000000100000000000000000035b3c9110004007f0000017f000001fb3c1900fb3c18fe0000003c000000010000000000000000b3c9003511000400".encode(encoding='utf_8'),("127.0.0.1",3000))
udpSocket.sendto(b"00050003000379a35e80c58622a55ab00000000000000000ac110002ac11000100000000000000000000000a0000034800002f4c0000527600000800000001000000000000000000ac110001ac11000200000000000000000000000a0000034800002f4c0000527600000000000001000000000000000000ac110001e00000fb000000000000000000000001000000a90000e01c0000e01c14e914e9000011000000000000000000",("127.0.0.1",3000))


(2130706433, 7788, 4214989963, 4215020796, 6, 10, 208, 164207)

(2130706433, 7788, 4214989963, 4215020796, 6, 10, 208, 164207)

In [55]:

#endcoding=utf-8
from socket import *
 
udpSocket=socket(AF_INET,SOCK_DGRAM)
 
udpSocket.bind(("",7788))  #参数是元组的形式
#使用udp发送的数据，在每一次的时候都需要写上接收方的IP和port
test1 = b"2130706433, 7788, 4214989963, 4215020796, 6, 10, 208, 164207"
udpSocket.sendto(test1,("127.0.0.1",3000))
udpSocket.sendto(b"00050003000379a35e80c58622a55ab00000000000000000ac110002ac11000100000000000000000000000a0000034800002f4c0000527600000800000001000000000000000000ac110001ac11000200000000000000000000000a0000034800002f4c0000527600000000000001000000000000000000ac110001e00000fb000000000000000000000001000000a90000e01c0000e01c14e914e9000011000000000000000000",("127.0.0.1",3000))


#(2130706433, 7788, 4214989963, 4215020796, 6, 10, 208, 164207)

336

In [ ]:

#endcoding=utf-8
import socket
s = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)
server_addr = ('127.0.0.1',9999)
s.bind(server_addr)
client_addr = ('127.0.0.1',3000) 
# udpSocket=socket(AF_INET,SOCK_DGRAM)
f = open("data/test data/test_data.json", 'rb')
count = 0
flag = 1

while True:

    data = f.read(1024)
    s.sendto(data,client_addr)
    print(str(count)+'byte')


 

    count+=1
print('recircled'+str(count))

 
#udpSocket.bind(("",7788))  #参数是元组的形式
#使用udp发送的数据，在每一次的时候都需要写上接收方的IP和port
#udpSocket.sendto("0009000a000000035c9f55980000000100000000000000400400000e00080004000c000400150004001600040001000400020004000a0004000e000400070002000b00020004000100060001003c000100050001000000400800000e001b0010001c001000150004001600040001000400020004000a0004000e000400070002000b00020004000100060001003c000100050001040001447f0000017f000001fb3c1aaafb3c18fd000190100000004b00000000000000000050942c061b04007f0000017f000001fb3c1aaafb3c18fd00000f94000000360000000000000000942c0050061f04007f0000017f000001fb3c1cfcfb3c1a9b0000d3fc0000002a000000000000000000509434061b04007f0000017f000001fb3c1cfcfb3c1a9b00000a490000001e000000000000000094340050061f04007f0000017f000001fb3bb82cfb3ba48b000002960000000300000000000000000050942a061904007f0000017f000001fb3bb82cfb3ba48b00000068000000020000000000000000942a0050061104007f0000017f000001fb3c1900fb3c18fe0000004c0000000100000000000000000035b3c9110004007f0000017f000001fb3c1900fb3c18fe0000003c000000010000000000000000b3c9003511000400".encode(encoding='utf_8'),("127.0.0.1",3000))
#udpSocket.sendto(b"00050003000379a35e80c58622a55ab00000000000000000ac110002ac11000100000000000000000000000a0000034800002f4c0000527600000800000001000000000000000000ac110001ac11000200000000000000000000000a0000034800002f4c0000527600000000000001000000000000000000ac110001e00000fb000000000000000000000001000000a90000e01c0000e01c14e914e9000011000000000000000000",("127.0.0.1",3000))



0byte
1byte
2byte
3byte
4byte
5byte
6byte
7byte
8byte
9byte
10byte
11byte
12byte
13byte
14byte
15byte
16byte
17byte
18byte
19byte
20byte
21byte
22byte
23byte
24byte
25byte
26byte
27byte
28byte
29byte
30byte
31byte
32byte
33byte
34byte
35byte
36byte
37byte
38byte
39byte
40byte
41byte
42byte
43byte
44byte
45byte
46byte
47byte
48byte
49byte
50byte
51byte
52byte
53byte
54byte
55byte
56byte
57byte
58byte
59byte
60byte
61byte
62byte
63byte
64byte
65byte
66byte
67byte
68byte
69byte
70byte
71byte
72byte
73byte
74byte
75byte
76byte
77byte
78byte
79byte
80byte
81byte
82byte
83byte
84byte
85byte
86byte
87byte
88byte
89byte
90byte
91byte
92byte
93byte
94byte
95byte
96byte
97byte
98byte
99byte
100byte
101byte
102byte
103byte
104byte
105byte
106byte
107byte
108byte
109byte
110byte
111byte
112byte
113byte
114byte
115byte
116byte
117byte
118byte
119byte
120byte
121byte
122byte
123byte
124byte
125byte
126byte
127byte
128byte
129byte
130byte
131byte
132byte
133byte
134byte
135byte
136byte
137byte
138byt

1414byte
1415byte
1416byte
1417byte
1418byte
1419byte
1420byte
1421byte
1422byte
1423byte
1424byte
1425byte
1426byte
1427byte
1428byte
1429byte
1430byte
1431byte
1432byte
1433byte
1434byte
1435byte
1436byte
1437byte
1438byte
1439byte
1440byte
1441byte
1442byte
1443byte
1444byte
1445byte
1446byte
1447byte
1448byte
1449byte
1450byte
1451byte
1452byte
1453byte
1454byte
1455byte
1456byte
1457byte
1458byte
1459byte
1460byte
1461byte
1462byte
1463byte
1464byte
1465byte
1466byte
1467byte
1468byte
1469byte
1470byte
1471byte
1472byte
1473byte
1474byte
1475byte
1476byte
1477byte
1478byte
1479byte
1480byte
1481byte
1482byte
1483byte
1484byte
1485byte
1486byte
1487byte
1488byte
1489byte
1490byte
1491byte
1492byte
1493byte
1494byte
1495byte
1496byte
1497byte
1498byte
1499byte
1500byte
1501byte
1502byte
1503byte
1504byte
1505byte
1506byte
1507byte
1508byte
1509byte
1510byte
1511byte
1512byte
1513byte
1514byte
1515byte
1516byte
1517byte
1518byte
1519byte
1520byte
1521byte
1522byte
1523byte
1524byte
1

2864byte
2865byte
2866byte
2867byte
2868byte
2869byte
2870byte
2871byte
2872byte
2873byte
2874byte
2875byte
2876byte
2877byte
2878byte
2879byte
2880byte
2881byte
2882byte
2883byte
2884byte
2885byte
2886byte
2887byte
2888byte
2889byte
2890byte
2891byte
2892byte
2893byte
2894byte
2895byte
2896byte
2897byte
2898byte
2899byte
2900byte
2901byte
2902byte
2903byte
2904byte
2905byte
2906byte
2907byte
2908byte
2909byte
2910byte
2911byte
2912byte
2913byte
2914byte
2915byte
2916byte
2917byte
2918byte
2919byte
2920byte
2921byte
2922byte
2923byte
2924byte
2925byte
2926byte
2927byte
2928byte
2929byte
2930byte
2931byte
2932byte
2933byte
2934byte
2935byte
2936byte
2937byte
2938byte
2939byte
2940byte
2941byte
2942byte
2943byte
2944byte
2945byte
2946byte
2947byte
2948byte
2949byte
2950byte
2951byte
2952byte
2953byte
2954byte
2955byte
2956byte
2957byte
2958byte
2959byte
2960byte
2961byte
2962byte
2963byte
2964byte
2965byte
2966byte
2967byte
2968byte
2969byte
2970byte
2971byte
2972byte
2973byte
2974byte
2

4307byte
4308byte
4309byte
4310byte
4311byte
4312byte
4313byte
4314byte
4315byte
4316byte
4317byte
4318byte
4319byte
4320byte
4321byte
4322byte
4323byte
4324byte
4325byte
4326byte
4327byte
4328byte
4329byte
4330byte
4331byte
4332byte
4333byte
4334byte
4335byte
4336byte
4337byte
4338byte
4339byte
4340byte
4341byte
4342byte
4343byte
4344byte
4345byte
4346byte
4347byte
4348byte
4349byte
4350byte
4351byte
4352byte
4353byte
4354byte
4355byte
4356byte
4357byte
4358byte
4359byte
4360byte
4361byte
4362byte
4363byte
4364byte
4365byte
4366byte
4367byte
4368byte
4369byte
4370byte
4371byte
4372byte
4373byte
4374byte
4375byte
4376byte
4377byte
4378byte
4379byte
4380byte
4381byte
4382byte
4383byte
4384byte
4385byte
4386byte
4387byte
4388byte
4389byte
4390byte
4391byte
4392byte
4393byte
4394byte
4395byte
4396byte
4397byte
4398byte
4399byte
4400byte
4401byte
4402byte
4403byte
4404byte
4405byte
4406byte
4407byte
4408byte
4409byte
4410byte
4411byte
4412byte
4413byte
4414byte
4415byte
4416byte
4417byte
4

5542byte
5543byte
5544byte
5545byte
5546byte
5547byte
5548byte
5549byte
5550byte
5551byte
5552byte
5553byte
5554byte
5555byte
5556byte
5557byte
5558byte
5559byte
5560byte
5561byte
5562byte
5563byte
5564byte
5565byte
5566byte
5567byte
5568byte
5569byte
5570byte
5571byte
5572byte
5573byte
5574byte
5575byte
5576byte
5577byte
5578byte
5579byte
5580byte
5581byte
5582byte
5583byte
5584byte
5585byte
5586byte
5587byte
5588byte
5589byte
5590byte
5591byte
5592byte
5593byte
5594byte
5595byte
5596byte
5597byte
5598byte
5599byte
5600byte
5601byte
5602byte
5603byte
5604byte
5605byte
5606byte
5607byte
5608byte
5609byte
5610byte
5611byte
5612byte
5613byte
5614byte
5615byte
5616byte
5617byte
5618byte
5619byte
5620byte
5621byte
5622byte
5623byte
5624byte
5625byte
5626byte
5627byte
5628byte
5629byte
5630byte
5631byte
5632byte
5633byte
5634byte
5635byte
5636byte
5637byte
5638byte
5639byte
5640byte
5641byte
5642byte
5643byte
5644byte
5645byte
5646byte
5647byte
5648byte
5649byte
5650byte
5651byte
5652byte
5

...

196927byte
196928byte
196929byte
196930byte
196931byte
196932byte
196933byte
196934byte
196935byte
196936byte
196937byte
196938byte
196939byte
196940byte
196941byte
196942byte
196943byte
196944byte
196945byte
196946byte
196947byte
196948byte
196949byte
196950byte
196951byte
196952byte
196953byte
196954byte
196955byte
196956byte
196957byte
196958byte
196959byte
196960byte
196961byte
196962byte
196963byte
196964byte
196965byte
196966byte
196967byte
196968byte
196969byte
196970byte
196971byte
196972byte
196973byte
196974byte
196975byte
196976byte
196977byte
196978byte
196979byte
196980byte
196981byte
196982byte
196983byte
196984byte
196985byte
196986byte
196987byte
196988byte
196989byte
196990byte
196991byte
196992byte
196993byte
196994byte
196995byte
196996byte
196997byte
196998byte
196999byte
197000byte
197001byte
197002byte
197003byte
197004byte
197005byte
197006byte
197007byte
197008byte
197009byte
197010byte
197011byte
197012byte
197013byte
197014byte
197015byte
197016byte
197017byte

198563byte
198564byte
198565byte
198566byte
198567byte
198568byte
198569byte
198570byte
198571byte
198572byte
198573byte
198574byte
198575byte
198576byte
198577byte
198578byte
198579byte
198580byte
198581byte
198582byte
198583byte
198584byte
198585byte
198586byte
198587byte
198588byte
198589byte
198590byte
198591byte
198592byte
198593byte
198594byte
198595byte
198596byte
198597byte
198598byte
198599byte
198600byte
198601byte
198602byte
198603byte
198604byte
198605byte
198606byte
198607byte
198608byte
198609byte
198610byte
198611byte
198612byte
198613byte
198614byte
198615byte
198616byte
198617byte
198618byte
198619byte
198620byte
198621byte
198622byte
198623byte
198624byte
198625byte
198626byte
198627byte
198628byte
198629byte
198630byte
198631byte
198632byte
198633byte
198634byte
198635byte
198636byte
198637byte
198638byte
198639byte
198640byte
198641byte
198642byte
198643byte
198644byte
198645byte
198646byte
198647byte
198648byte
198649byte
198650byte
198651byte
198652byte
198653byte

199917byte
199918byte
199919byte
199920byte
199921byte
199922byte
199923byte
199924byte
199925byte
199926byte
199927byte
199928byte
199929byte
199930byte
199931byte
199932byte
199933byte
199934byte
199935byte
199936byte
199937byte
199938byte
199939byte
199940byte
199941byte
199942byte
199943byte
199944byte
199945byte
199946byte
199947byte
199948byte
199949byte
199950byte
199951byte
199952byte
199953byte
199954byte
199955byte
199956byte
199957byte
199958byte
199959byte
199960byte
199961byte
199962byte
199963byte
199964byte
199965byte
199966byte
199967byte
199968byte
199969byte
199970byte
199971byte
199972byte
199973byte
199974byte
199975byte
199976byte
199977byte
199978byte
199979byte
199980byte
199981byte
199982byte
199983byte
199984byte
199985byte
199986byte
199987byte
199988byte
199989byte
199990byte
199991byte
199992byte
199993byte
199994byte
199995byte
199996byte
199997byte
199998byte
199999byte
200000byte
200001byte
200002byte
200003byte
200004byte
200005byte
200006byte
200007byte

201257byte
201258byte
201259byte
201260byte
201261byte
201262byte
201263byte
201264byte
201265byte
201266byte
201267byte
201268byte
201269byte
201270byte
201271byte
201272byte
201273byte
201274byte
201275byte
201276byte
201277byte
201278byte
201279byte
201280byte
201281byte
201282byte
201283byte
201284byte
201285byte
201286byte
201287byte
201288byte
201289byte
201290byte
201291byte
201292byte
201293byte
201294byte
201295byte
201296byte
201297byte
201298byte
201299byte
201300byte
201301byte
201302byte
201303byte
201304byte
201305byte
201306byte
201307byte
201308byte
201309byte
201310byte
201311byte
201312byte
201313byte
201314byte
201315byte
201316byte
201317byte
201318byte
201319byte
201320byte
201321byte
201322byte
201323byte
201324byte
201325byte
201326byte
201327byte
201328byte
201329byte
201330byte
201331byte
201332byte
201333byte
201334byte
201335byte
201336byte
201337byte
201338byte
201339byte
201340byte
201341byte
201342byte
201343byte
201344byte
201345byte
201346byte
201347byte

202620byte
202621byte
202622byte
202623byte
202624byte
202625byte
202626byte
202627byte
202628byte
202629byte
202630byte
202631byte
202632byte
202633byte
202634byte
202635byte
202636byte
202637byte
202638byte
202639byte
202640byte
202641byte
202642byte
202643byte
202644byte
202645byte
202646byte
202647byte
202648byte
202649byte
202650byte
202651byte
202652byte
202653byte
202654byte
202655byte
202656byte
202657byte
202658byte
202659byte
202660byte
202661byte
202662byte
202663byte
202664byte
202665byte
202666byte
202667byte
202668byte
202669byte
202670byte
202671byte
202672byte
202673byte
202674byte
202675byte
202676byte
202677byte
202678byte
202679byte
202680byte
202681byte
202682byte
202683byte
202684byte
202685byte
202686byte
202687byte
202688byte
202689byte
202690byte
202691byte
202692byte
202693byte
202694byte
202695byte
202696byte
202697byte
202698byte
202699byte
202700byte
202701byte
202702byte
202703byte
202704byte
202705byte
202706byte
202707byte
202708byte
202709byte
202710byte

### Through above code we can listen port 3000, and handel every flows, store them as ***.gz

In [16]:
data = 0009000a000000035c9f55980000000100000000000000400400000e00080004000c000400150004001600040001000400020004000a0004000e000400070002000b00020004000100060001003c000100050001000000400800000e001b0010001c001000150004001600040001000400020004000a0004000e000400070002000b00020004000100060001003c000100050001040001447f0000017f000001fb3c1aaafb3c18fd000190100000004b00000000000000000050942c061b04007f0000017f000001fb3c1aaafb3c18fd00000f94000000360000000000000000942c0050061f04007f0000017f000001fb3c1cfcfb3c1a9b0000d3fc0000002a000000000000000000509434061b04007f0000017f000001fb3c1cfcfb3c1a9b00000a490000001e000000000000000094340050061f04007f0000017f000001fb3bb82cfb3ba48b000002960000000300000000000000000050942a061904007f0000017f000001fb3bb82cfb3ba48b00000068000000020000000000000000942a0050061104007f0000017f000001fb3c1900fb3c18fe0000004c0000000100000000000000000035b3c9110004007f0000017f000001fb3c1900fb3c18fe0000003c000000010000000000000000b3c9003511000400

dec = data.decode()
data = bytes.fromhex(dec)
print(data)

SyntaxError: invalid token (<ipython-input-16-ad14546ce4b3>, line 1)

In [15]:
import sys
print(sys.path.append('/home/yuhao/Study/master thesis/python-netflow-v9-softflowd/netflow/'))

None


In [ ]:
# convert timestamp to time
1585497478

In [9]:
list1 = list({'IPV4_SRC_ADDR': '127.0.0.1', 'IPV4_DST_ADDR': '127.0.0.1', 'LAST_SWITCHED': 4215020202, 'FIRST_SWITCHED': 4215019773, 'IN_BYTES': 102416, 'IN_PKTS': 75, 'INPUT_SNMP': 0, 'OUTPUT_SNMP': 0, 'L4_SRC_PORT': 80, 'L4_DST_PORT': 37932, 'PROTOCOL': 6, 'TCP_FLAGS': 27, 'IP_PROTOCOL_VERSION': 4, 'SRC_TOS': 0}, {'IPV4_SRC_ADDR': '127.0.0.1', 'IPV4_DST_ADDR': '127.0.0.1', 'LAST_SWITCHED': 4215020202, 'FIRST_SWITCHED': 4215019773, 'IN_BYTES': 3988, 'IN_PKTS': 54, 'INPUT_SNMP': 0, 'OUTPUT_SNMP': 0, 'L4_SRC_PORT': 37932, 'L4_DST_PORT': 80, 'PROTOCOL': 6, 'TCP_FLAGS': 31, 'IP_PROTOCOL_VERSION': 4, 'SRC_TOS': 0},{'IPV4_SRC_ADDR': '127.0.0.1', 'IPV4_DST_ADDR': '127.0.0.1', 'LAST_SWITCHED': 4215020202, 'FIRST_SWITCHED': 4215019773, 'IN_BYTES': 3988, 'IN_PKTS': 54, 'INPUT_SNMP': 0, 'OUTPUT_SNMP': 0, 'L4_SRC_PORT': 37932, 'L4_DST_PORT': 80, 'PROTOCOL': 6, 'TCP_FLAGS': 31, 'IP_PROTOCOL_VERSION': 4, 'SRC_TOS': 0})

TypeError: list() takes at most 1 argument (3 given)

In [12]:
list1 = []
list1.append({'IPV4_SRC_ADDR': '127.0.0.1', 'IPV4_DST_ADDR': '127.0.0.1', 'LAST_SWITCHED': 4215020202, 'FIRST_SWITCHED': 4215019773, 'IN_BYTES': 3988, 'IN_PKTS': 54, 'INPUT_SNMP': 0, 'OUTPUT_SNMP': 0, 'L4_SRC_PORT': 37932, 'L4_DST_PORT': 80, 'PROTOCOL': 6, 'TCP_FLAGS': 31, 'IP_PROTOCOL_VERSION': 4, 'SRC_TOS': 0})

In [13]:
list1.append({'IPV4_SRC_ADDR': '127.0.0.2', 'IPV4_DST_ADDR': '127.0.0.1', 'LAST_SWITCHED': 4215020202, 'FIRST_SWITCHED': 4215019773, 'IN_BYTES': 3988, 'IN_PKTS': 54, 'INPUT_SNMP': 0, 'OUTPUT_SNMP': 0, 'L4_SRC_PORT': 37932, 'L4_DST_PORT': 80, 'PROTOCOL': 6, 'TCP_FLAGS': 31, 'IP_PROTOCOL_VERSION': 4, 'SRC_TOS': 0})

In [14]:
list1.append({'IPV4_SRC_ADDR': '127.0.0.3', 'IPV4_DST_ADDR': '127.0.0.1', 'LAST_SWITCHED': 4215020202, 'FIRST_SWITCHED': 4215019773, 'IN_BYTES': 3988, 'IN_PKTS': 54, 'INPUT_SNMP': 0, 'OUTPUT_SNMP': 0, 'L4_SRC_PORT': 37932, 'L4_DST_PORT': 80, 'PROTOCOL': 6, 'TCP_FLAGS': 31, 'IP_PROTOCOL_VERSION': 4, 'SRC_TOS': 0})

In [15]:
list1

[{'IPV4_SRC_ADDR': '127.0.0.1',
  'IPV4_DST_ADDR': '127.0.0.1',
  'LAST_SWITCHED': 4215020202,
  'FIRST_SWITCHED': 4215019773,
  'IN_BYTES': 3988,
  'IN_PKTS': 54,
  'INPUT_SNMP': 0,
  'OUTPUT_SNMP': 0,
  'L4_SRC_PORT': 37932,
  'L4_DST_PORT': 80,
  'PROTOCOL': 6,
  'TCP_FLAGS': 31,
  'IP_PROTOCOL_VERSION': 4,
  'SRC_TOS': 0},
 {'IPV4_SRC_ADDR': '127.0.0.2',
  'IPV4_DST_ADDR': '127.0.0.1',
  'LAST_SWITCHED': 4215020202,
  'FIRST_SWITCHED': 4215019773,
  'IN_BYTES': 3988,
  'IN_PKTS': 54,
  'INPUT_SNMP': 0,
  'OUTPUT_SNMP': 0,
  'L4_SRC_PORT': 37932,
  'L4_DST_PORT': 80,
  'PROTOCOL': 6,
  'TCP_FLAGS': 31,
  'IP_PROTOCOL_VERSION': 4,
  'SRC_TOS': 0},
 {'IPV4_SRC_ADDR': '127.0.0.3',
  'IPV4_DST_ADDR': '127.0.0.1',
  'LAST_SWITCHED': 4215020202,
  'FIRST_SWITCHED': 4215019773,
  'IN_BYTES': 3988,
  'IN_PKTS': 54,
  'INPUT_SNMP': 0,
  'OUTPUT_SNMP': 0,
  'L4_SRC_PORT': 37932,
  'L4_DST_PORT': 80,
  'PROTOCOL': 6,
  'TCP_FLAGS': 31,
  'IP_PROTOCOL_VERSION': 4,
  'SRC_TOS': 0}]

In [18]:
list1[0]

{'IPV4_SRC_ADDR': '127.0.0.1',
 'IPV4_DST_ADDR': '127.0.0.1',
 'LAST_SWITCHED': 4215020202,
 'FIRST_SWITCHED': 4215019773,
 'IN_BYTES': 3988,
 'IN_PKTS': 54,
 'INPUT_SNMP': 0,
 'OUTPUT_SNMP': 0,
 'L4_SRC_PORT': 37932,
 'L4_DST_PORT': 80,
 'PROTOCOL': 6,
 'TCP_FLAGS': 31,
 'IP_PROTOCOL_VERSION': 4,
 'SRC_TOS': 0}

In [1]:
"""
This file belongs to https://github.com/bitkeks/python-netflow-v9-softflowd.

The test packets (defined below as hex streams) were extracted from "real"
softflowd exports based on a sample PCAP capture file.

Copyright 2016-2020 Dominik Pataky <software+pynetflow@dpataky.eu>
Licensed under MIT License. See LICENSE.
"""

# The flowset with 2 templates (IPv4 and IPv6) and 8 flows with data
import queue
import random
import socket
import time
import threading
import logging
import socketserver
from collections import namedtuple

from package.ipfix import IPFIXTemplateNotRecognized
#from package.utils import *
from package.utils import UnknownExportVersion, parse_packet, flow_filter_v4, flow_filter_v6
from package.v9 import V9TemplateNotRecognized

RawPacket = namedtuple('RawPacket', ['ts', 'client', 'data'])
ParsedPacket = namedtuple('ParsedPacket', ['ts', 'client', 'export'])

PACKET_TIMEOUT = 60 * 60

logger = logging.getLogger("netflow-collector")
ch = logging.StreamHandler()
formatter = logging.Formatter('%(asctime)s - %(levelname)s - %(message)s')
ch.setFormatter(formatter)
logger.addHandler(ch)



class QueuingRequestHandler(socketserver.BaseRequestHandler):
    def handle(self):
        data = self.request[0]  # get content, [1] would be the socket
        self.server.queue.put(RawPacket(time.time(), self.client_address, data))
        logger.debug(
            "Received %d bytes of data from %s", len(data), self.client_address
        )


class QueuingUDPListener(socketserver.ThreadingUDPServer):
    """A threaded UDP server that adds a (time, data) tuple to a queue for
    every request it sees
    """

    def __init__(self, interface, queue):
        self.queue = queue

        # If IPv6 interface addresses are used, override the default AF_INET family
        if ":" in interface[0]:
            self.address_family = socket.AF_INET6

        super().__init__(interface, QueuingRequestHandler)

class ThreadedNetFlowListener(threading.Thread):
    """A thread that listens for incoming NetFlow packets, processes them, and
    makes them available to consumers.
    - When initialized, will start listening for NetFlow packets on the provided
      host and port and queuing them for processing.
    - When started, will start processing and parsing queued packets.
    - When stopped, will shut down the listener and stop processing.
    - When joined, will wait for the listener to exit
    For example, a simple script that outputs data until killed with CTRL+C:
    >>> listener = ThreadedNetFlowListener('0.0.0.0', 2055)
    >>> print("Listening for NetFlow packets")
    >>> listener.start() # start processing packets
    >>> try:
    ...     while True:
    ...         ts, export = listener.get()
    ...         print("Time: {}".format(ts))
    ...         for f in export.flows:
    ...             print(" - {IPV4_SRC_ADDR} sent data to {IPV4_DST_ADDR}"
    ...                   "".format(**f))
    ... finally:
    ...     print("Stopping...")
    ...     listener.stop()
    ...     listener.join()
    ...     print("Stopped!")
    """

    def __init__(self, host: str, port: int):
        logger.info("Starting the NetFlow listener on {}:{}".format(host, port))
        self.output = queue.Queue()
        self.input = queue.Queue()
        self.server = QueuingUDPListener((host, port), self.input)
        self.thread = threading.Thread(target=self.server.serve_forever)
        self.thread.start()
        self._shutdown = threading.Event()
        super().__init__()

    def get(self, block=True, timeout=None) -> ParsedPacket:
        """Get a processed flow.
        If optional args 'block' is true and 'timeout' is None (the default),
        block if necessary until a flow is available. If 'timeout' is
        a non-negative number, it blocks at most 'timeout' seconds and raises
        the queue.Empty exception if no flow was available within that time.
        Otherwise ('block' is false), return a flow if one is immediately
        available, else raise the queue.Empty exception ('timeout' is ignored
        in that case).
        """
        return self.output.get(block, timeout)

    def run(self):
        # Process packets from the queue
        try:
            templates = {"netflow": {}, "ipfix": {}}
            to_retry = []
            while not self._shutdown.is_set():
                try:
                    # 0.5s delay to limit CPU usage while waiting for new packets
                    pkt = self.input.get(block=True, timeout=0.5)  # type: RawPacket
                except queue.Empty:
                    continue

                try:
                    # templates is passed as reference, updated in V9ExportPacket
                    export = parse_packet(pkt.data, templates)
                except UnknownExportVersion as e:
                    logger.error("%s, ignoring the packet", e)
                    continue
                except (V9TemplateNotRecognized, IPFIXTemplateNotRecognized):
                    # TODO: differentiate between v9 and IPFIX, use separate to_retry lists
                    if time.time() - pkt.ts > PACKET_TIMEOUT:
                        logger.warning("Dropping an old and undecodable v9/IPFIX ExportPacket")
                    else:
                        to_retry.append(pkt)
                        logger.debug("Failed to decode a v9/IPFIX ExportPacket - will "
                                     "re-attempt when a new template is discovered")
                    continue

                if export.header.version == 10:
                    logger.debug("Processed an IPFIX ExportPacket with length %d.", export.header.length)
                else:
                    logger.debug("Processed a v%d ExportPacket with %d flows.",
                                 export.header.version, export.header.count)

                # If any new templates were discovered, dump the unprocessable
                # data back into the queue and try to decode them again
                if export.header.version in [9, 10] and export.contains_new_templates and to_retry:
                    logger.debug("Received new template(s)")
                    logger.debug("Will re-attempt to decode %d old v9/IPFIX ExportPackets", len(to_retry))
                    for p in to_retry:
                        self.input.put(p)
                    to_retry.clear()

                self.output.put(ParsedPacket(pkt.ts, pkt.client, export))
        finally:
            # Only reached when while loop ends
            self.server.shutdown()
            self.server.server_close()

    def stop(self):
        logger.info("Shutting down the NetFlow listener")
        self._shutdown.set()

    def join(self, timeout=None):
        self.thread.join(timeout=timeout)
        super().join(timeout=timeout)




# Invalid export hex stream
PACKET_INVALID = "FFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFFF"

CONNECTION = ('127.0.0.1', 3000)
NUM_PACKETS = 1000


def emit_packets(packets, delay=0.0001):
    """Send the provided packets to the listener"""
    sock = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)
    for p in packets:
        sock.sendto(bytes.fromhex(p), CONNECTION)
        time.sleep(delay)
    sock.close()


def send_recv_packets(packets, delay=0.0001, store_packets=-1) -> (list, float, float):
    """Starts a listener, send packets, receives packets

    returns a tuple: ([(ts, export), ...], time_started_sending, time_stopped_sending)
    """
    #listener = ThreadedNetFlowListener(*CONNECTION)
    tstart = time.time()
    emit_packets(packets, delay=delay)
    time.sleep(0.5)  # Allow packets to be sent and recieved
    tend = time.time()
    #listener.start()

    pkts = []
    to_pad = 0
    while True:
        try:
            #packet = listener.get(timeout=0.5)
            if -1 == store_packets or store_packets > 0:
                # Case where a programm yields from the queue and stores all packets.
                #pkts.append(packet)
                if store_packets != -1 and len(pkts) > store_packets:
                    to_pad += len(pkts)  # Hack for testing
                    pkts.clear()
            else:
                # Performance measurements for cases where yielded objects are processed
                # immediatelly instead of stored. Add empty tuple to retain counting possibility.
                pkts.append(())
        except queue.Empty:
            break
    listener.stop()
    listener.join()
    if to_pad > 0:
        pkts = [()] * to_pad + pkts
    return pkts, tstart, tend


def generate_packets(amount, version, template_every_x=100):
    packets = [PACKET_IPFIX]
    template = PACKET_IPFIX_TEMPLATE

    if version == 1:
        packets = [PACKET_V1]
    elif version == 5:
        packets = [PACKET_V5]
    elif version == 9:
        packets = [*PACKETS_V9]
        template = PACKET_V9_TEMPLATE

    if amount < template_every_x:
        template_every_x = 10

    # If the list of test packets is only one item big (the same packet is used over and over),
    # do not use random.choice - it costs performance and results in the same packet every time.
    def single_packet(pkts):
        return pkts[0]

    packet_func = single_packet
    if len(packets) > 1:
        packet_func = random.choice

    for x in range(amount):
        if x % template_every_x == 0 and version in [9, 10]:
            # First packet always a template, then periodically
            # Note: this was once based on random.random, but it costs performance
            yield template
        else:
            yield packet_func(packets)


# Example export for v1 which contains two flows from one ICMP ping request/reply session
PACKET_V1 = "000100020001189b5e80c32c2fd41848ac110002ac11000100000000000000000000000a00000348" \
            "000027c700004af100000800000001000000000000000000ac110001ac1100020000000000000000" \
            "0000000a00000348000027c700004af100000000000001000000000000000000"

# Example export for v5 which contains three flows, two for ICMP ping and one multicast on interface (224.0.0.251)
PACKET_V5 = "00050003000379a35e80c58622a55ab00000000000000000ac110002ac1100010000000000000000" \
            "0000000a0000034800002f4c0000527600000800000001000000000000000000ac110001ac110002" \
            "00000000000000000000000a0000034800002f4c0000527600000000000001000000000000000000" \
            "ac110001e00000fb000000000000000000000001000000a90000e01c0000e01c14e914e900001100" \
            "0000000000000000"

PACKET_V9_TEMPLATE = "0009000a000000035c9f55980000000100000000000000400400000e00080004000c000400150004" \
                     "001600040001000400020004000a0004000e000400070002000b00020004000100060001003c0001" \
                     "00050001000000400800000e001b0010001c001000150004001600040001000400020004000a0004" \
                     "000e000400070002000b00020004000100060001003c000100050001040001447f0000017f000001" \
                     "fb3c1aaafb3c18fd000190100000004b00000000000000000050942c061b04007f0000017f000001" \
                     "fb3c1aaafb3c18fd00000f94000000360000000000000000942c0050061f04007f0000017f000001" \
                     "fb3c1cfcfb3c1a9b0000d3fc0000002a000000000000000000509434061b04007f0000017f000001" \
                     "fb3c1cfcfb3c1a9b00000a490000001e000000000000000094340050061f04007f0000017f000001" \
                     "fb3bb82cfb3ba48b000002960000000300000000000000000050942a061904007f0000017f000001" \
                     "fb3bb82cfb3ba48b00000068000000020000000000000000942a0050061104007f0000017f000001" \
                     "fb3c1900fb3c18fe0000004c0000000100000000000000000035b3c9110004007f0000017f000001" \
                     "fb3c1900fb3c18fe0000003c000000010000000000000000b3c9003511000400"

# This packet is special. We take PACKET_V9_TEMPLATE and re-order the templates and flows.
# The first line is the header, the smaller lines the templates and the long lines the flows (limited to 80 chars)
PACKET_V9_TEMPLATE_MIXED = ("0009000a000000035c9f55980000000100000000"  # header
                            "040001447f0000017f000001fb3c1aaafb3c18fd000190100000004b00000000000000000050942c"
                            "061b04007f0000017f000001fb3c1aaafb3c18fd00000f94000000360000000000000000942c0050"
                            "061f04007f0000017f000001fb3c1cfcfb3c1a9b0000d3fc0000002a000000000000000000509434"
                            "061b04007f0000017f000001fb3c1cfcfb3c1a9b00000a490000001e000000000000000094340050"
                            "061f04007f0000017f000001fb3bb82cfb3ba48b000002960000000300000000000000000050942a"
                            "061904007f0000017f000001fb3bb82cfb3ba48b00000068000000020000000000000000942a0050"
                            "061104007f0000017f000001fb3c1900fb3c18fe0000004c0000000100000000000000000035b3c9"
                            "110004007f0000017f000001fb3c1900fb3c18fe0000003c000000010000000000000000b3c90035"
                            "11000400"  # end of flow segments
                            "000000400400000e00080004000c000400150004001600040001000400020004"  # template 1024
                            "000a0004000e000400070002000b00020004000100060001003c000100050001"
                            "000000400800000e001b0010001c001000150004001600040001000400020004"  # template 2048
                            "000a0004000e000400070002000b00020004000100060001003c000100050001")

# Three packets without templates, each with 12 flows
PACKETS_V9 = [
    "0009000c000000035c9f55980000000200000000040001e47f0000017f000001fb3c1a17fb3c19fd"
    "000001480000000200000000000000000035ea82110004007f0000017f000001fb3c1a17fb3c19fd"
    "0000007a000000020000000000000000ea820035110004007f0000017f000001fb3c1a17fb3c19fd"
    "000000f80000000200000000000000000035c6e2110004007f0000017f000001fb3c1a17fb3c19fd"
    "0000007a000000020000000000000000c6e20035110004007f0000017f000001fb3c1a9efb3c1a9c"
    "0000004c0000000100000000000000000035adc1110004007f0000017f000001fb3c1a9efb3c1a9c"
    "0000003c000000010000000000000000adc10035110004007f0000017f000001fb3c1b74fb3c1b72"
    "0000004c0000000100000000000000000035d0b3110004007f0000017f000001fb3c1b74fb3c1b72"
    "0000003c000000010000000000000000d0b30035110004007f0000017f000001fb3c2f59fb3c1b71"
    "00001a350000000a000000000000000000509436061b04007f0000017f000001fb3c2f59fb3c1b71"
    "0000038a0000000a000000000000000094360050061b04007f0000017f000001fb3c913bfb3c9138"
    "0000004c0000000100000000000000000035e262110004007f0000017f000001fb3c913bfb3c9138"
    "0000003c000000010000000000000000e262003511000400",

    "0009000c000000035c9f55980000000300000000040001e47f0000017f000001fb3ca523fb3c913b"
    "0000030700000005000000000000000000509438061b04007f0000017f000001fb3ca523fb3c913b"
    "000002a200000005000000000000000094380050061b04007f0000017f000001fb3f7fe1fb3dbc97"
    "0002d52800000097000000000000000001bb8730061b04007f0000017f000001fb3f7fe1fb3dbc97"
    "0000146c000000520000000000000000873001bb061f04007f0000017f000001fb3d066ffb3d066c"
    "0000004c0000000100000000000000000035e5bd110004007f0000017f000001fb3d066ffb3d066c"
    "0000003c000000010000000000000000e5bd0035110004007f0000017f000001fb3d1a61fb3d066b"
    "000003060000000500000000000000000050943a061b04007f0000017f000001fb3d1a61fb3d066b"
    "000002a2000000050000000000000000943a0050061b04007f0000017f000001fb3fed00fb3f002c"
    "0000344000000016000000000000000001bbae50061f04007f0000017f000001fb3fed00fb3f002c"
    "00000a47000000120000000000000000ae5001bb061b04007f0000017f000001fb402f17fb402a75"
    "0003524c000000a5000000000000000001bbc48c061b04007f0000017f000001fb402f17fb402a75"
    "000020a60000007e0000000000000000c48c01bb061f0400",

    "0009000c000000035c9f55980000000400000000040001e47f0000017f000001fb3d7ba2fb3d7ba0"
    "0000004c0000000100000000000000000035a399110004007f0000017f000001fb3d7ba2fb3d7ba0"
    "0000003c000000010000000000000000a3990035110004007f0000017f000001fb3d8f85fb3d7b9f"
    "000003070000000500000000000000000050943c061b04007f0000017f000001fb3d8f85fb3d7b9f"
    "000002a2000000050000000000000000943c0050061b04007f0000017f000001fb3d9165fb3d7f6d"
    "0000c97b0000002a000000000000000001bbae48061b04007f0000017f000001fb3d9165fb3d7f6d"
    "000007f40000001a0000000000000000ae4801bb061b04007f0000017f000001fb3dbc96fb3dbc7e"
    "0000011e0000000200000000000000000035bd4f110004007f0000017f000001fb3dbc96fb3dbc7e"
    "0000008e000000020000000000000000bd4f0035110004007f0000017f000001fb3ddbb3fb3c1a18"
    "0000bfee0000002f00000000000000000050ae56061b04007f0000017f000001fb3ddbb3fb3c1a18"
    "00000982000000270000000000000000ae560050061b04007f0000017f000001fb3ddbb3fb3c1a18"
    "0000130e0000001200000000000000000050e820061b04007f0000017f000001fb3ddbb3fb3c1a18"
    "0000059c000000140000000000000000e8200050061b0400"
]

# Example export for IPFIX (v10) with 4 templates, 1 option template and 8 data flow sets
PACKET_IPFIX_TEMPLATE = "000a05202d45a4700000001300000000000200400400000e00080004000c00040016000400150004" \
                        "0001000400020004000a0004000e000400070002000b00020004000100060001003c000100050001" \
                        "000200340401000b00080004000c000400160004001500040001000400020004000a0004000e0004" \
                        "00200002003c000100050001000200400800000e001b0010001c0010001600040015000400010004" \
                        "00020004000a0004000e000400070002000b00020004000100060001003c00010005000100020034" \
                        "0801000b001b0010001c001000160004001500040001000400020004000a0004000e0004008b0002" \
                        "003c0001000500010003001e010000050001008f000400a000080131000401320004013000020100" \
                        "001a00000a5900000171352e672100000001000000000001040000547f000001ac110002ff7ed688" \
                        "ff7ed73a000015c70000000d000000000000000001bbe1a6061b0400ac1100027f000001ff7ed688" \
                        "ff7ed73a0000074f000000130000000000000000e1a601bb061f04000401004cac110002ac110001" \
                        "ff7db9e0ff7dc1d0000000fc00000003000000000000000008000400ac110001ac110002ff7db9e0" \
                        "ff7dc1d0000000fc0000000300000000000000000000040008010220fde66f14e0f1960900000242" \
                        "ac110002ff0200000000000000000001ff110001ff7dfad6ff7e0e95000001b00000000600000000" \
                        "0000000087000600fde66f14e0f196090000affeaffeaffefdabcdef123456789000000000000001" \
                        "ff7e567fff7e664a0000020800000005000000000000000080000600fde66f14e0f1960900000000" \
                        "00000001fde66f14e0f196090000affeaffeaffeff7e567fff7e664a000002080000000500000000" \
                        "0000000081000600fe800000000000000042aafffe73bbfafde66f14e0f196090000affeaffeaffe" \
                        "ff7e6aaaff7e6aaa0000004800000001000000000000000087000600fde66f14e0f1960900000242" \
                        "ac110002fe800000000000000042aafffe73bbfaff7e6aaaff7e6aaa000000400000000100000000" \
                        "0000000088000600fe800000000000000042acfffe110002fe800000000000000042aafffe73bbfa" \
                        "ff7e7eaaff7e7eaa0000004800000001000000000000000087000600fe800000000000000042aaff" \
                        "fe73bbfafe800000000000000042acfffe110002ff7e7eaaff7e7eaa000000400000000100000000" \
                        "0000000088000600fe800000000000000042aafffe73bbfafe800000000000000042acfffe110002" \
                        "ff7e92aaff7e92aa0000004800000001000000000000000087000600fe800000000000000042acff" \
                        "fe110002fe800000000000000042aafffe73bbfaff7e92aaff7e92aa000000400000000100000000" \
                        "000000008800060008000044fde66f14e0f196090000affeaffeaffefd41b7143f86000000000000" \
                        "00000001ff7ec2a0ff7ec2a00000004a000000010000000000000000d20100351100060004000054" \
                        "ac1100027f000001ff7ed62eff7ed68700000036000000010000000000000000c496003511000400" \
                        "7f000001ac110002ff7ed62eff7ed687000000760000000100000000000000000035c49611000400" \
                        "08000044fde66f14e0f196090000affeaffeaffefd41b7143f8600000000000000000001ff7ef359" \
                        "ff7ef3590000004a000000010000000000000000b1e700351100060004000054ac1100027f000001" \
                        "ff7f06e4ff7f06e800000036000000010000000000000000a8f90035110004007f000001ac110002" \
                        "ff7f06e4ff7f06e8000000a60000000100000000000000000035a8f911000400"

# Example export for IPFIX with two data sets
PACKET_IPFIX = "000a00d02d45a47000000016000000000801007cfe800000000000000042acfffe110002fde66f14" \
               "e0f196090000000000000001ff7f0755ff7f07550000004800000001000000000000000087000600" \
               "fdabcdef123456789000000000000001fe800000000000000042acfffe110002ff7f0755ff7f0755" \
               "000000400000000100000000000000008800060008000044fde66f14e0f196090000affeaffeaffe" \
               "2a044e42020000000000000000000223ff7f06e9ff7f22d500000140000000040000000000000000" \
               "e54c01bb06020600"

PACKET_IPFIX_TEMPLATE_ETHER = "000a05002d45a4700000000d00000000" \
                              "000200500400001200080004000c000400160004001500040001000400020004000a0004000e0004" \
                              "00070002000b00020004000100060001003c000100050001003a0002003b00020038000600390006" \
                              "000200440401000f00080004000c000400160004001500040001000400020004000a0004000e0004" \
                              "00200002003c000100050001003a0002003b000200380006003900060002005008000012001b0010" \
                              "001c001000160004001500040001000400020004000a0004000e000400070002000b000200040001" \
                              "00060001003c000100050001003a0002003b00020038000600390006000200440801000f001b0010" \
                              "001c001000160004001500040001000400020004000a0004000e0004008b0002003c000100050001" \
                              "003a0002003b000200380006003900060003001e010000050001008f000400a00008013100040132" \
                              "0004013000020100001a00000009000000b0d80a558000000001000000000001040000747f000001" \
                              "ac110002e58b988be58b993e000015c70000000d000000000000000001bbe1a6061b040000000000" \
                              "123456affefeaffeaffeaffeac1100027f000001e58b988be58b993e0000074f0000001300000000" \
                              "00000000e1a601bb061f040000000000affeaffeaffe123456affefe0401006cac110002ac110001" \
                              "e58a7be3e58a83d3000000fc0000000300000000000000000800040000000000affeaffeaffe0242" \
                              "aa73bbfaac110001ac110002e58a7be3e58a83d3000000fc00000003000000000000000000000400" \
                              "00000000123456affefeaffeaffeaffe080102b0fde66f14e0f196090000affeaffeaffeff020000" \
                              "0000000000000001ff110001e58abcd9e58ad098000001b000000006000000000000000087000600" \
                              "00000000affeaffeaffe3333ff110001fde66f14e0f196090000affeaffeaffefde66f14e0f19609" \
                              "0000000000000001e58b1883e58b284e000002080000000500000000000000008000060000000000" \
                              "affeaffeaffe123456affefefdabcdef123456789000000000000001fde66f14e0f1960900000242" \
                              "ac110002e58b1883e58b284e0000020800000005000000000000000081000600000000000242aa73" \
                              "bbfaaffeaffeaffefe800000000000000042aafffe73bbfafde66f14e0f196090000affeaffeaffe" \
                              "e58b2caee58b2cae000000480000000100000000000000008700060000000000123456affefe0242" \
                              "ac110002fde66f14e0f196090000affeaffeaffefe800000000000000042aafffe73bbfae58b2cae" \
                              "e58b2cae000000400000000100000000000000008800060000000000affeaffeaffe123456affefe" \
                              "fe800000000000000042acfffe110002fe800000000000000042aafffe73bbfae58b40aee58b40ae" \
                              "000000480000000100000000000000008700060000000000affeaffeaffe123456affefefe800000" \
                              "000000000042aafffe73bbfafe800000000000000042acfffe110002e58b40aee58b40ae00000040" \
                              "0000000100000000000000008800060000000000123456affefeaffeaffeaffefe80000000000000" \
                              "0042aafffe73bbfafe800000000000000042acfffe110002e58b54aee58b54ae0000004800000001" \
                              "00000000000000008700060000000000123456affefeaffeaffeaffefe800000000000000042acff" \
                              "fe110002fe800000000000000042aafffe73bbfae58b54aee58b54ae000000400000000100000000" \
                              "000000008800060000000000affeaffeaffe123456affefe"

PACKET_IPFIX_ETHER = "000a02905e8b0aa90000001600000000" \
                     "08000054fde66f14e0f196090000affeaffeaffefd40abcdabcd00000000000000011111e58b84a4" \
                     "e58b84a40000004a000000010000000000000000d20100351100060000000000affeaffeaffe0242" \
                     "aa73bbfa04000074ac1100027f000001e58b9831e58b988a00000036000000010000000000000000" \
                     "c49600351100040000000000affeaffeaffe123456affefe7f000001ac110002e58b9831e58b988a" \
                     "000000760000000100000000000000000035c4961100040000000000123456affefeaffeaffeaffe" \
                     "08000054fde66f14e0f196090000affeaffeaffefd40abcdabcd00000000000000011111e58bb55c" \
                     "e58bb55c0000004a000000010000000000000000b1e700351100060000000000affeaffeaffe0242" \
                     "aa73bbfa04000074ac1100027f000001e58bc8e8e58bc8ec00000036000000010000000000000000" \
                     "a8f900351100040000000000affeaffeaffe123456affefe7f000001ac110002e58bc8e8e58bc8ec" \
                     "000000a60000000100000000000000000035a8f91100040000000000123456affefeaffeaffeaffe" \
                     "0801009cfe800000000000000042acfffe110002fdabcdef123456789000000000000001e58bc958" \
                     "e58bc958000000480000000100000000000000008700060000000000affeaffeaffe123456affefe" \
                     "fdabcdef123456789000000000000001fe800000000000000042acfffe110002e58bc958e58bc958" \
                     "000000400000000100000000000000008800060000000000123456affefeaffeaffeaffe08000054" \
                     "fde66f14e0f196090000affeaffeaffe2a044e42020000000000000000000223e58bc8ede58be4d8" \
                     "00000140000000040000000000000000e54c01bb0602060000000000affeaffeaffe123456affefe"


In [ ]:
def gen_pkts(n, idx):
            for x in range(n):
                if x == idx:
                    yield PACKET_V9_TEMPLATE
                else:
                    yield random.choice(PACKETS_V9)

pkts, tstart, tend = send_recv_packets(generate_packets(100000, 9), delay=0)

In [25]:
CONNECTION = ('127.0.0.1', 3000)
NUM_PACKETS = 1000


def emit_packets(packets, delay=0.0001):
    """Send the provided packets to the listener"""
    sock = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)
    for p in packets:
        sock.sendto(bytes.fromhex(p), CONNECTION)
        time.sleep(delay)
    sock.close()
    
emit_packets(gen_pkts(10, [PACKET_V5]), delay=0)

In [17]:
test1 = '0009000a000000035c9f55980000000100000000000000400400000e00080004000c000400150004001600040001000400020004000a0004000e000400070002000b00020004000100060001003c000100050001000000400800000e001b0010001c001000150004001600040001000400020004000a0004000e000400070002000b00020004000100060001003c000100050001040001447f0000017f000001fb3c1aaafb3c18fd000190100000004b00000000000000000050942c061b04007f0000017f000001fb3c1aaafb3c18fd00000f94000000360000000000000000942c0050061f04007f0000017f000001fb3c1cfcfb3c1a9b0000d3fc0000002a000000000000000000509434061b04007f0000017f000001fb3c1cfcfb3c1a9b00000a490000001e000000000000000094340050061f04007f0000017f000001fb3bb82cfb3ba48b000002960000000300000000000000000050942a061904007f0000017f000001fb3bb82cfb3ba48b00000068000000020000000000000000942a0050061104007f0000017f000001fb3c1900fb3c18fe0000004c0000000100000000000000000035b3c9110004007f0000017f000001fb3c1900fb3c18fe0000003c000000010000000000000000b3c9003511000400'
#test2 = bytes.fromhex(test1)
#str1 = bytes.fromhex(test1).decode('utf-16-le')
if type(test1) == str:
        # hex dump as string
        str1 = bytes.fromhex(test1)
elif type(test1) == bytes:
        # check representation based on utf-8 decoding result
        dec = test1.decode()
        str1 = bytes.fromhex(dec)
str1

b'\x00\t\x00\n\x00\x00\x00\x03\\\x9fU\x98\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00@\x04\x00\x00\x0e\x00\x08\x00\x04\x00\x0c\x00\x04\x00\x15\x00\x04\x00\x16\x00\x04\x00\x01\x00\x04\x00\x02\x00\x04\x00\n\x00\x04\x00\x0e\x00\x04\x00\x07\x00\x02\x00\x0b\x00\x02\x00\x04\x00\x01\x00\x06\x00\x01\x00<\x00\x01\x00\x05\x00\x01\x00\x00\x00@\x08\x00\x00\x0e\x00\x1b\x00\x10\x00\x1c\x00\x10\x00\x15\x00\x04\x00\x16\x00\x04\x00\x01\x00\x04\x00\x02\x00\x04\x00\n\x00\x04\x00\x0e\x00\x04\x00\x07\x00\x02\x00\x0b\x00\x02\x00\x04\x00\x01\x00\x06\x00\x01\x00<\x00\x01\x00\x05\x00\x01\x04\x00\x01D\x7f\x00\x00\x01\x7f\x00\x00\x01\xfb<\x1a\xaa\xfb<\x18\xfd\x00\x01\x90\x10\x00\x00\x00K\x00\x00\x00\x00\x00\x00\x00\x00\x00P\x94,\x06\x1b\x04\x00\x7f\x00\x00\x01\x7f\x00\x00\x01\xfb<\x1a\xaa\xfb<\x18\xfd\x00\x00\x0f\x94\x00\x00\x006\x00\x00\x00\x00\x00\x00\x00\x00\x94,\x00P\x06\x1f\x04\x00\x7f\x00\x00\x01\x7f\x00\x00\x01\xfb<\x1c\xfc\xfb<\x1a\x9b\x00\x00\xd3\xfc\x00\x00\x00*\x00\x00\x00\x00\x00\x00\x00\x00\x00P\x94

In [19]:
import struct
struct.unpack('!H', str1[:2])[0]

9

In [28]:
from package.v1 import V1ExportPacket
from package.v5 import V5ExportPacket
from package.v9 import V9ExportPacket

templates = {"netflow": {}, "ipfix": {}}
version = 9
if version == 1:
        print(V1ExportPacket(data))
elif version == 5:
        print(V5ExportPacket(data))
elif version == 9:
        print(V9ExportPacket(data, templates["netflow"]).flows)
        print(V9ExportPacket.flows)

[<DataRecord with data: {'IPV4_SRC_ADDR': '127.0.0.1', 'IPV4_DST_ADDR': '127.0.0.1', 'LAST_SWITCHED': 4215020202, 'FIRST_SWITCHED': 4215019773, 'IN_BYTES': 102416, 'IN_PKTS': 75, 'INPUT_SNMP': 0, 'OUTPUT_SNMP': 0, 'L4_SRC_PORT': 80, 'L4_DST_PORT': 37932, 'PROTOCOL': 6, 'TCP_FLAGS': 27, 'IP_PROTOCOL_VERSION': 4, 'SRC_TOS': 0}>, <DataRecord with data: {'IPV4_SRC_ADDR': '127.0.0.1', 'IPV4_DST_ADDR': '127.0.0.1', 'LAST_SWITCHED': 4215020202, 'FIRST_SWITCHED': 4215019773, 'IN_BYTES': 3988, 'IN_PKTS': 54, 'INPUT_SNMP': 0, 'OUTPUT_SNMP': 0, 'L4_SRC_PORT': 37932, 'L4_DST_PORT': 80, 'PROTOCOL': 6, 'TCP_FLAGS': 31, 'IP_PROTOCOL_VERSION': 4, 'SRC_TOS': 0}>, <DataRecord with data: {'IPV4_SRC_ADDR': '127.0.0.1', 'IPV4_DST_ADDR': '127.0.0.1', 'LAST_SWITCHED': 4215020796, 'FIRST_SWITCHED': 4215020187, 'IN_BYTES': 54268, 'IN_PKTS': 42, 'INPUT_SNMP': 0, 'OUTPUT_SNMP': 0, 'L4_SRC_PORT': 80, 'L4_DST_PORT': 37940, 'PROTOCOL': 6, 'TCP_FLAGS': 27, 'IP_PROTOCOL_VERSION': 4, 'SRC_TOS': 0}>, <DataRecord with d